# BERT for Multi-Label Classification
Refer post : https://medium.com/@javaid.nabi/building-a-multi-label-text-classifier-using-bert-and-tensorflow-f188e0ecdc5d

In [1]:
import os
import collections
import pandas as pd
import tensorflow as tf
import tensorflow_hub as hub
from datetime import datetime

W0516 18:37:49.443778 15132 __init__.py:56] Some hub symbols are not available because TensorFlow version is less than 1.14


In [3]:
##install bert if not already done
##!pip install bert-tensorflow

In [2]:
import bert
from bert import run_classifier
from bert import optimization
from bert import tokenization
from bert import modeling

In [3]:
##use downloaded model, change path accordingly
BERT_VOCAB= './uncased_L-12_H-768_A-12/vocab.txt'
BERT_INIT_CHKPNT = './uncased_L-12_H-768_A-12/bert_model.ckpt'
BERT_CONFIG = './uncased_L-12_H-768_A-12/bert_config.json'

In [4]:
tokenization.validate_case_matches_checkpoint(True,BERT_INIT_CHKPNT)
tokenizer = tokenization.FullTokenizer(
      vocab_file=BERT_VOCAB, do_lower_case=True)

In [5]:

tokenizer.tokenize("This here's an example of using the BERT tokenizer")

['this',
 'here',
 "'",
 's',
 'an',
 'example',
 'of',
 'using',
 'the',
 'bert',
 'token',
 '##izer']

In [7]:
##change path accordingly
train_data_path='./Download/train.csv'
train = pd.read_csv(train_data_path)
test = pd.read_csv('./Download/test.csv')

In [8]:
train.head()

id                                       comment_text  toxic  \
0  0000997932d777bf  Explanation\nWhy the edits made under my usern...      0   
1  000103f0d9cfb60f  D'aww! He matches this background colour I'm s...      0   
2  000113f07ec002fd  Hey man, I'm really not trying to edit war. It...      0   
3  0001b41b1c6bb37e  "\nMore\nI can't make any real suggestions on ...      0   
4  0001d958c54c6e35  You, sir, are my hero. Any chance you remember...      0   

   severe_toxic  obscene  threat  insult  identity_hate  
0             0        0       0       0              0  
1             0        0       0       0              0  
2             0        0       0       0              0  
3             0        0       0       0              0  
4             0        0       0       0              0

In [9]:
ID = 'id'
DATA_COLUMN = 'comment_text'
LABEL_COLUMNS = ['toxic','severe_toxic','obscene','threat','insult','identity_hate']

In [10]:
class InputExample(object):
    """A single training/test example for simple sequence classification."""

    def __init__(self, guid, text_a, text_b=None, labels=None):
        """Constructs a InputExample.

        Args:
            guid: Unique id for the example.
            text_a: string. The untokenized text of the first sequence. For single
            sequence tasks, only this sequence must be specified.
            text_b: (Optional) string. The untokenized text of the second sequence.
            Only must be specified for sequence pair tasks.
            labels: (Optional) [string]. The label of the example. This should be
            specified for train and dev examples, but not for test examples.
        """
        self.guid = guid
        self.text_a = text_a
        self.text_b = text_b
        self.labels = labels


class InputFeatures(object):
    """A single set of features of data."""

    def __init__(self, input_ids, input_mask, segment_ids, label_ids, is_real_example=True):
        self.input_ids = input_ids
        self.input_mask = input_mask
        self.segment_ids = segment_ids
        self.label_ids = label_ids,
        self.is_real_example=is_real_example

In [11]:
def create_examples(df, labels_available=True):
    """Creates examples for the training and dev sets."""
    examples = []
    for (i, row) in enumerate(df.values):
        guid = row[0]
        text_a = row[1]
        if labels_available:
            labels = row[2:]
        else:
            labels = [0,0,0,0,0,0]
        examples.append(
            InputExample(guid=guid, text_a=text_a, labels=labels))
    return examples

In [12]:
TRAIN_VAL_RATIO = 0.9
LEN = train.shape[0]
SIZE_TRAIN = int(TRAIN_VAL_RATIO*LEN)

x_train = train[:10000]
x_val = train[SIZE_TRAIN:]

train_examples = create_examples(x_train)

In [13]:
def convert_examples_to_features(examples,  max_seq_length, tokenizer):
    """Loads a data file into a list of `InputBatch`s."""

    features = []
    for (ex_index, example) in enumerate(examples):
        print(example.text_a)
        tokens_a = tokenizer.tokenize(example.text_a)

        tokens_b = None
        if example.text_b:
            tokens_b = tokenizer.tokenize(example.text_b)
            # Modifies `tokens_a` and `tokens_b` in place so that the total
            # length is less than the specified length.
            # Account for [CLS], [SEP], [SEP] with "- 3"
            _truncate_seq_pair(tokens_a, tokens_b, max_seq_length - 3)
        else:
            # Account for [CLS] and [SEP] with "- 2"
            if len(tokens_a) > max_seq_length - 2:
                tokens_a = tokens_a[:(max_seq_length - 2)]

        # The convention in BERT is:
        # (a) For sequence pairs:
        #  tokens:   [CLS] is this jack ##son ##ville ? [SEP] no it is not . [SEP]
        #  type_ids: 0   0  0    0    0     0       0 0    1  1  1  1   1 1
        # (b) For single sequences:
        #  tokens:   [CLS] the dog is hairy . [SEP]
        #  type_ids: 0   0   0   0  0     0 0
        #
        # Where "type_ids" are used to indicate whether this is the first
        # sequence or the second sequence. The embedding vectors for `type=0` and
        # `type=1` were learned during pre-training and are added to the wordpiece
        # embedding vector (and position vector). This is not *strictly* necessary
        # since the [SEP] token unambigiously separates the sequences, but it makes
        # it easier for the model to learn the concept of sequences.
        #
        # For classification tasks, the first vector (corresponding to [CLS]) is
        # used as as the "sentence vector". Note that this only makes sense because
        # the entire model is fine-tuned.
        tokens = ["[CLS]"] + tokens_a + ["[SEP]"]
        segment_ids = [0] * len(tokens)

        if tokens_b:
            tokens += tokens_b + ["[SEP]"]
            segment_ids += [1] * (len(tokens_b) + 1)

        input_ids = tokenizer.convert_tokens_to_ids(tokens)

        # The mask has 1 for real tokens and 0 for padding tokens. Only real
        # tokens are attended to.
        input_mask = [1] * len(input_ids)

        # Zero-pad up to the sequence length.
        padding = [0] * (max_seq_length - len(input_ids))
        input_ids += padding
        input_mask += padding
        segment_ids += padding

        assert len(input_ids) == max_seq_length
        assert len(input_mask) == max_seq_length
        assert len(segment_ids) == max_seq_length
        
        labels_ids = []
        for label in example.labels:
            labels_ids.append(int(label))

        if ex_index < 0:
            logger.info("*** Example ***")
            logger.info("guid: %s" % (example.guid))
            logger.info("tokens: %s" % " ".join(
                    [str(x) for x in tokens]))
            logger.info("input_ids: %s" % " ".join([str(x) for x in input_ids]))
            logger.info("input_mask: %s" % " ".join([str(x) for x in input_mask]))
            logger.info(
                    "segment_ids: %s" % " ".join([str(x) for x in segment_ids]))
            logger.info("label: %s (id = %s)" % (example.labels, labels_ids))

        features.append(
                InputFeatures(input_ids=input_ids,
                              input_mask=input_mask,
                              segment_ids=segment_ids,
                              label_ids=labels_ids))
    return features

In [14]:
# We'll set sequences to be at most 128 tokens long.
MAX_SEQ_LENGTH = 128

In [27]:
# Compute train and warmup steps from batch size
# These hyperparameters are copied from this colab notebook (https://colab.sandbox.google.com/github/tensorflow/tpu/blob/master/tools/colab/bert_finetuning_with_cloud_tpus.ipynb)
BATCH_SIZE = 16
LEARNING_RATE = 2e-5
NUM_TRAIN_EPOCHS = 1.0
# Warmup is a period of time where hte learning rate 
# is small and gradually increases--usually helps training.
WARMUP_PROPORTION = 0.1
# Model configs
SAVE_CHECKPOINTS_STEPS = 1000
SAVE_SUMMARY_STEPS = 500

In [16]:
class PaddingInputExample(object):
    """Fake example so the num input examples is a multiple of the batch size.
    When running eval/predict on the TPU, we need to pad the number of examples
    to be a multiple of the batch size, because the TPU requires a fixed batch
    size. The alternative is to drop the last batch, which is bad because it means
    the entire output data won't be generated.
    We use this class instead of `None` because treating `None` as padding
    battches could cause silent errors.
    """
    
    
def convert_single_example(ex_index, example, max_seq_length,
                           tokenizer):
    """Converts a single `InputExample` into a single `InputFeatures`."""

    if isinstance(example, PaddingInputExample):
        return InputFeatures(
            input_ids=[0] * max_seq_length,
            input_mask=[0] * max_seq_length,
            segment_ids=[0] * max_seq_length,
            label_ids=0,
            is_real_example=False)

    tokens_a = tokenizer.tokenize(example.text_a)
    tokens_b = None
    if example.text_b:
        tokens_b = tokenizer.tokenize(example.text_b)

    if tokens_b:
        # Modifies `tokens_a` and `tokens_b` in place so that the total
        # length is less than the specified length.
        # Account for [CLS], [SEP], [SEP] with "- 3"
        _truncate_seq_pair(tokens_a, tokens_b, max_seq_length - 3)
    else:
        # Account for [CLS] and [SEP] with "- 2"
        if len(tokens_a) > max_seq_length - 2:
            tokens_a = tokens_a[0:(max_seq_length - 2)]

    # The convention in BERT is:
    # (a) For sequence pairs:
    #  tokens:   [CLS] is this jack ##son ##ville ? [SEP] no it is not . [SEP]
    #  type_ids: 0     0  0    0    0     0       0 0     1  1  1  1   1 1
    # (b) For single sequences:
    #  tokens:   [CLS] the dog is hairy . [SEP]
    #  type_ids: 0     0   0   0  0     0 0
    #
    # Where "type_ids" are used to indicate whether this is the first
    # sequence or the second sequence. The embedding vectors for `type=0` and
    # `type=1` were learned during pre-training and are added to the wordpiece
    # embedding vector (and position vector). This is not *strictly* necessary
    # since the [SEP] token unambiguously separates the sequences, but it makes
    # it easier for the model to learn the concept of sequences.
    #
    # For classification tasks, the first vector (corresponding to [CLS]) is
    # used as the "sentence vector". Note that this only makes sense because
    # the entire model is fine-tuned.
    tokens = []
    segment_ids = []
    tokens.append("[CLS]")
    segment_ids.append(0)
    for token in tokens_a:
        tokens.append(token)
        segment_ids.append(0)
    tokens.append("[SEP]")
    segment_ids.append(0)

    if tokens_b:
        for token in tokens_b:
            tokens.append(token)
            segment_ids.append(1)
        tokens.append("[SEP]")
        segment_ids.append(1)

    input_ids = tokenizer.convert_tokens_to_ids(tokens)

    # The mask has 1 for real tokens and 0 for padding tokens. Only real
    # tokens are attended to.
    input_mask = [1] * len(input_ids)

    # Zero-pad up to the sequence length.
    while len(input_ids) < max_seq_length:
        input_ids.append(0)
        input_mask.append(0)
        segment_ids.append(0)

    assert len(input_ids) == max_seq_length
    assert len(input_mask) == max_seq_length
    assert len(segment_ids) == max_seq_length

    labels_ids = []
    for label in example.labels:
        labels_ids.append(int(label))


    feature = InputFeatures(
        input_ids=input_ids,
        input_mask=input_mask,
        segment_ids=segment_ids,
        label_ids=labels_ids,
        is_real_example=True)
    return feature


def file_based_convert_examples_to_features(
        examples, max_seq_length, tokenizer, output_file):
    """Convert a set of `InputExample`s to a TFRecord file."""

    writer = tf.python_io.TFRecordWriter(output_file)

    for (ex_index, example) in enumerate(examples):
        #if ex_index % 10000 == 0:
            #tf.logging.info("Writing example %d of %d" % (ex_index, len(examples)))

        feature = convert_single_example(ex_index, example,
                                         max_seq_length, tokenizer)

        def create_int_feature(values):
            f = tf.train.Feature(int64_list=tf.train.Int64List(value=list(values)))
            return f

        features = collections.OrderedDict()
        features["input_ids"] = create_int_feature(feature.input_ids)
        features["input_mask"] = create_int_feature(feature.input_mask)
        features["segment_ids"] = create_int_feature(feature.segment_ids)
        features["is_real_example"] = create_int_feature(
            [int(feature.is_real_example)])
        if isinstance(feature.label_ids, list):
            label_ids = feature.label_ids
        else:
            label_ids = feature.label_ids[0]
        features["label_ids"] = create_int_feature(label_ids)

        tf_example = tf.train.Example(features=tf.train.Features(feature=features))
        writer.write(tf_example.SerializeToString())
    writer.close()


def file_based_input_fn_builder(input_file, seq_length, is_training,
                                drop_remainder):
    """Creates an `input_fn` closure to be passed to TPUEstimator."""

    name_to_features = {
        "input_ids": tf.FixedLenFeature([seq_length], tf.int64),
        "input_mask": tf.FixedLenFeature([seq_length], tf.int64),
        "segment_ids": tf.FixedLenFeature([seq_length], tf.int64),
        "label_ids": tf.FixedLenFeature([6], tf.int64),
        "is_real_example": tf.FixedLenFeature([], tf.int64),
    }

    def _decode_record(record, name_to_features):
        """Decodes a record to a TensorFlow example."""
        example = tf.parse_single_example(record, name_to_features)

        # tf.Example only supports tf.int64, but the TPU only supports tf.int32.
        # So cast all int64 to int32.
        for name in list(example.keys()):
            t = example[name]
            if t.dtype == tf.int64:
                t = tf.to_int32(t)
            example[name] = t

        return example

    def input_fn(params):
        """The actual input function."""
        batch_size = params["batch_size"]

        # For training, we want a lot of parallel reading and shuffling.
        # For eval, we want no shuffling and parallel reading doesn't matter.
        d = tf.data.TFRecordDataset(input_file)
        if is_training:
            d = d.repeat()
            d = d.shuffle(buffer_size=100)

        d = d.apply(
            tf.contrib.data.map_and_batch(
                lambda record: _decode_record(record, name_to_features),
                batch_size=batch_size,
                drop_remainder=drop_remainder))

        return d

    return input_fn


def _truncate_seq_pair(tokens_a, tokens_b, max_length):
    """Truncates a sequence pair in place to the maximum length."""

    # This is a simple heuristic which will always truncate the longer sequence
    # one token at a time. This makes more sense than truncating an equal percent
    # of tokens from each, since if one sequence is very short then each token
    # that's truncated likely contains more information than a longer sequence.
    while True:
        total_length = len(tokens_a) + len(tokens_b)
        if total_length <= max_length:
            break
        if len(tokens_a) > len(tokens_b):
            tokens_a.pop()
        else:
            tokens_b.pop()

In [17]:
# Compute # train and warmup steps from batch size
num_train_steps = int(len(train_examples) / BATCH_SIZE * NUM_TRAIN_EPOCHS)
num_warmup_steps = int(num_train_steps * WARMUP_PROPORTION)

In [20]:
train_file = os.path.join('./working/train.tf_record')
#filename = Path(train_file)
if not os.path.exists(train_file):
    open(train_file, 'w').close()

In [21]:
file_based_convert_examples_to_features(
            train_examples, MAX_SEQ_LENGTH, tokenizer, train_file)
tf.logging.info("***** Running training *****")
tf.logging.info("  Num examples = %d", len(train_examples))
tf.logging.info("  Batch size = %d", BATCH_SIZE)
tf.logging.info("  Num steps = %d", num_train_steps)

INFO:tensorflow:***** Running training *****


I0516 19:00:02.199422 15132 tf_logging.py:115] ***** Running training *****


INFO:tensorflow:  Num examples = 10000


I0516 19:00:02.201420 15132 tf_logging.py:115]   Num examples = 10000


INFO:tensorflow:  Batch size = 32


I0516 19:00:02.204424 15132 tf_logging.py:115]   Batch size = 32


INFO:tensorflow:  Num steps = 312


I0516 19:00:02.207425 15132 tf_logging.py:115]   Num steps = 312


In [22]:
train_input_fn = file_based_input_fn_builder(
    input_file=train_file,
    seq_length=MAX_SEQ_LENGTH,
    is_training=True,
    drop_remainder=True)

In [23]:
def create_model(bert_config, is_training, input_ids, input_mask, segment_ids,
                 labels, num_labels, use_one_hot_embeddings):
    """Creates a classification model."""
    model = modeling.BertModel(
        config=bert_config,
        is_training=is_training,
        input_ids=input_ids,
        input_mask=input_mask,
        token_type_ids=segment_ids,
        use_one_hot_embeddings=use_one_hot_embeddings)

    # In the demo, we are doing a simple classification task on the entire
    # segment.
    #
    # If you want to use the token-level output, use model.get_sequence_output()
    # instead.
    output_layer = model.get_pooled_output()

    hidden_size = output_layer.shape[-1].value

    output_weights = tf.get_variable(
        "output_weights", [num_labels, hidden_size],
        initializer=tf.truncated_normal_initializer(stddev=0.02))

    output_bias = tf.get_variable(
        "output_bias", [num_labels], initializer=tf.zeros_initializer())

    with tf.variable_scope("loss"):
        if is_training:
            # I.e., 0.1 dropout
            output_layer = tf.nn.dropout(output_layer, keep_prob=0.9)

        logits = tf.matmul(output_layer, output_weights, transpose_b=True)
        logits = tf.nn.bias_add(logits, output_bias)
        
        # probabilities = tf.nn.softmax(logits, axis=-1) ### multiclass case
        probabilities = tf.nn.sigmoid(logits)#### multi-label case
        
        labels = tf.cast(labels, tf.float32)
        tf.logging.info("num_labels:{};logits:{};labels:{}".format(num_labels, logits, labels))
        per_example_loss = tf.nn.sigmoid_cross_entropy_with_logits(labels=labels, logits=logits)
        loss = tf.reduce_mean(per_example_loss)

        # probabilities = tf.nn.softmax(logits, axis=-1)
        # log_probs = tf.nn.log_softmax(logits, axis=-1)
        #
        # one_hot_labels = tf.one_hot(labels, depth=num_labels, dtype=tf.float32)
        #
        # per_example_loss = -tf.reduce_sum(one_hot_labels * log_probs, axis=-1)
        # loss = tf.reduce_mean(per_example_loss)

        return (loss, per_example_loss, logits, probabilities)


def model_fn_builder(bert_config, num_labels, init_checkpoint, learning_rate,
                     num_train_steps, num_warmup_steps, use_tpu,
                     use_one_hot_embeddings):
    """Returns `model_fn` closure for TPUEstimator."""

    def model_fn(features, labels, mode, params):  # pylint: disable=unused-argument
        """The `model_fn` for TPUEstimator."""

        #tf.logging.info("*** Features ***")
        #for name in sorted(features.keys()):
        #    tf.logging.info("  name = %s, shape = %s" % (name, features[name].shape))

        input_ids = features["input_ids"]
        input_mask = features["input_mask"]
        segment_ids = features["segment_ids"]
        label_ids = features["label_ids"]
        is_real_example = None
        if "is_real_example" in features:
             is_real_example = tf.cast(features["is_real_example"], dtype=tf.float32)
        else:
             is_real_example = tf.ones(tf.shape(label_ids), dtype=tf.float32)

        is_training = (mode == tf.estimator.ModeKeys.TRAIN)

        (total_loss, per_example_loss, logits, probabilities) = create_model(
            bert_config, is_training, input_ids, input_mask, segment_ids, label_ids,
            num_labels, use_one_hot_embeddings)

        tvars = tf.trainable_variables()
        initialized_variable_names = {}
        scaffold_fn = None
        if init_checkpoint:
            (assignment_map, initialized_variable_names
             ) = modeling.get_assignment_map_from_checkpoint(tvars, init_checkpoint)
            if use_tpu:

                def tpu_scaffold():
                    tf.train.init_from_checkpoint(init_checkpoint, assignment_map)
                    return tf.train.Scaffold()

                scaffold_fn = tpu_scaffold
            else:
                tf.train.init_from_checkpoint(init_checkpoint, assignment_map)

        tf.logging.info("**** Trainable Variables ****")
        for var in tvars:
            init_string = ""
            if var.name in initialized_variable_names:
                init_string = ", *INIT_FROM_CKPT*"
            #tf.logging.info("  name = %s, shape = %s%s", var.name, var.shape,init_string)

        output_spec = None
        if mode == tf.estimator.ModeKeys.TRAIN:

            train_op = optimization.create_optimizer(
                total_loss, learning_rate, num_train_steps, num_warmup_steps, use_tpu)

            output_spec = tf.estimator.EstimatorSpec(
                mode=mode,
                loss=total_loss,
                train_op=train_op,
                scaffold=scaffold_fn)
        elif mode == tf.estimator.ModeKeys.EVAL:

            def metric_fn(per_example_loss, label_ids, probabilities, is_real_example):

                logits_split = tf.split(probabilities, num_labels, axis=-1)
                label_ids_split = tf.split(label_ids, num_labels, axis=-1)
                # metrics change to auc of every class
                eval_dict = {}
                for j, logits in enumerate(logits_split):
                    label_id_ = tf.cast(label_ids_split[j], dtype=tf.int32)
                    current_auc, update_op_auc = tf.metrics.auc(label_id_, logits)
                    eval_dict[str(j)] = (current_auc, update_op_auc)
                eval_dict['eval_loss'] = tf.metrics.mean(values=per_example_loss)
                return eval_dict

                ## original eval metrics
                # predictions = tf.argmax(logits, axis=-1, output_type=tf.int32)
                # accuracy = tf.metrics.accuracy(
                #     labels=label_ids, predictions=predictions, weights=is_real_example)
                # loss = tf.metrics.mean(values=per_example_loss, weights=is_real_example)
                # return {
                #     "eval_accuracy": accuracy,
                #     "eval_loss": loss,
                # }

            eval_metrics = metric_fn(per_example_loss, label_ids, probabilities, is_real_example)
            output_spec = tf.estimator.EstimatorSpec(
                mode=mode,
                loss=total_loss,
                eval_metric_ops=eval_metrics,
                scaffold=scaffold_fn)
        else:
            print("mode:", mode,"probabilities:", probabilities)
            output_spec = tf.estimator.EstimatorSpec(
                mode=mode,
                predictions={"probabilities": probabilities},
                scaffold=scaffold_fn)
        return output_spec

    return model_fn

In [24]:
OUTPUT_DIR = "./working/output"
# Specify outpit directory and number of checkpoint steps to save
run_config = tf.estimator.RunConfig(
    model_dir=OUTPUT_DIR,
    save_summary_steps=SAVE_SUMMARY_STEPS,
    keep_checkpoint_max=1,
    save_checkpoints_steps=SAVE_CHECKPOINTS_STEPS)

In [28]:
bert_config = modeling.BertConfig.from_json_file(BERT_CONFIG)
model_fn = model_fn_builder(
  bert_config=bert_config,
  num_labels= len(LABEL_COLUMNS),
  init_checkpoint=BERT_INIT_CHKPNT,
  learning_rate=LEARNING_RATE,
  num_train_steps=num_train_steps,
  num_warmup_steps=num_warmup_steps,
  use_tpu=False,
  use_one_hot_embeddings=False)

estimator = tf.estimator.Estimator(
  model_fn=model_fn,
  config=run_config,
  params={"batch_size": BATCH_SIZE})

INFO:tensorflow:Using config: {'_model_dir': './working/output', '_tf_random_seed': None, '_save_summary_steps': 500, '_save_checkpoints_steps': 1000, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 1, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x0000020E7B8AA9E8>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


I0516 19:02:55.172772 15132 tf_logging.py:115] Using config: {'_model_dir': './working/output', '_tf_random_seed': None, '_save_summary_steps': 500, '_save_checkpoints_steps': 1000, '_save_checkpoints_secs': None, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 1, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x0000020E7B8AA9E8>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


In [29]:
print(f'Beginning Training!')
current_time = datetime.now()
estimator.train(input_fn=train_input_fn, max_steps=num_train_steps)
print("Training took time ", datetime.now() - current_time)

Beginning Training!
INFO:tensorflow:Calling model_fn.


I0516 19:03:01.192768 15132 tf_logging.py:115] Calling model_fn.


INFO:tensorflow:num_labels:6;logits:Tensor("loss/BiasAdd:0", shape=(16, 6), dtype=float32);labels:Tensor("loss/Cast:0", shape=(16, 6), dtype=float32)


I0516 19:03:03.401793 15132 tf_logging.py:115] num_labels:6;logits:Tensor("loss/BiasAdd:0", shape=(16, 6), dtype=float32);labels:Tensor("loss/Cast:0", shape=(16, 6), dtype=float32)


INFO:tensorflow:**** Trainable Variables ****


...

INFO:tensorflow:Saving checkpoints for 312 into ./working/output\model.ckpt.


I0516 19:06:06.384862 15132 tf_logging.py:115] Saving checkpoints for 312 into ./working/output\model.ckpt.


INFO:tensorflow:Loss for final step: 0.057269484.


I0516 19:06:19.756862 15132 tf_logging.py:115] Loss for final step: 0.057269484.


Training took time  0:03:18.641095


In [30]:
eval_file = os.path.join('./working', "eval.tf_record")
#filename = Path(train_file)
if not os.path.exists(eval_file):
    open(eval_file, 'w').close()

eval_examples = create_examples(x_val)
file_based_convert_examples_to_features(
    eval_examples, MAX_SEQ_LENGTH, tokenizer, eval_file)

In [31]:
# This tells the estimator to run through the entire set.
eval_steps = None

eval_drop_remainder = False
eval_input_fn = file_based_input_fn_builder(
    input_file=eval_file,
    seq_length=MAX_SEQ_LENGTH,
    is_training=False,
    drop_remainder=False)

result = estimator.evaluate(input_fn=eval_input_fn, steps=eval_steps)

INFO:tensorflow:Calling model_fn.


I0516 19:07:32.624058 15132 tf_logging.py:115] Calling model_fn.


INFO:tensorflow:num_labels:6;logits:Tensor("loss/BiasAdd:0", shape=(?, 6), dtype=float32);labels:Tensor("loss/Cast:0", shape=(?, 6), dtype=float32)


I0516 19:07:34.820059 15132 tf_logging.py:115] num_labels:6;logits:Tensor("loss/BiasAdd:0", shape=(?, 6), dtype=float32);labels:Tensor("loss/Cast:0", shape=(?, 6), dtype=float32)


INFO:tensorflow:**** Trainable Variables ****


...

I0516 19:09:22.722302 15132 tf_logging.py:115] Finished evaluation at 2019-05-16-17:09:22


INFO:tensorflow:Saving dict for global step 312: 0 = 0.97484094, 1 = 0.97997785, 2 = 0.9776638, 3 = 0.89763963, 4 = 0.9750648, 5 = 0.93448246, eval_loss = 0.060002346, global_step = 312, loss = 0.06000276


I0516 19:09:22.724302 15132 tf_logging.py:115] Saving dict for global step 312: 0 = 0.97484094, 1 = 0.97997785, 2 = 0.9776638, 3 = 0.89763963, 4 = 0.9750648, 5 = 0.93448246, eval_loss = 0.060002346, global_step = 312, loss = 0.06000276


INFO:tensorflow:Saving 'checkpoint_path' summary for global step 312: ./working/output\model.ckpt-312


I0516 19:09:29.152302 15132 tf_logging.py:115] Saving 'checkpoint_path' summary for global step 312: ./working/output\model.ckpt-312


In [32]:
output_eval_file = os.path.join("./working", "eval_results.txt")
with tf.gfile.GFile(output_eval_file, "w") as writer:
    tf.logging.info("***** Eval results *****")
    for key in sorted(result.keys()):
        tf.logging.info("  %s = %s", key, str(result[key]))
        writer.write("%s = %s\n" % (key, str(result[key])))

INFO:tensorflow:***** Eval results *****


I0516 19:09:33.634172 15132 tf_logging.py:115] ***** Eval results *****


INFO:tensorflow:  0 = 0.97484094


I0516 19:09:33.635174 15132 tf_logging.py:115]   0 = 0.97484094


INFO:tensorflow:  1 = 0.97997785


...

I0516 19:09:33.643174 15132 tf_logging.py:115]   eval_loss = 0.060002346


INFO:tensorflow:  global_step = 312


I0516 19:09:33.645174 15132 tf_logging.py:115]   global_step = 312


INFO:tensorflow:  loss = 0.06000276


I0516 19:09:33.646176 15132 tf_logging.py:115]   loss = 0.06000276


In [33]:
x_test = test[125000:140000]
x_test = x_test.reset_index(drop=True)
predict_examples = create_examples(x_test,False)

In [34]:
test_features = convert_examples_to_features(predict_examples, MAX_SEQ_LENGTH, tokenizer)

a.k.a. Argument W/A Dumbass
:::::::If have just read this crap correctly you have just said that Hesperian is an arsehole. That to me is a personal attack. Now please clarify in simple straight forward english what you mean, if it the way have read considered yourself warned for WP:NPA and remove the comment.
:::::::A lengthy history in constructing the country is not relevant to how important the group is to the country? That seems to make little sense.
" 

 ::::::: Yes, I know; it's a fucking disease. Much of it is spread by editors acting in good faith, as they're unaware of the issues. That needs to change. Any gratuitous styling such as colour can and should be removed by any editor at any time. Deviations from site-wide norms require a much more solid rationale than ""ILIKEIT"". See WP:Deviations: In general, styles for tables and other block-level elements should be set using CSS classes, not with inline style attributes. 
 ::::::: We should talk about you sig, too; it's using t

and i am a retard ^_^
Robert 

 Can you contact me please at work. Brian Neson  Limnoporus
appointing these five RS sites as our panel of judges
Btw... could also tell you 1000 sites that say that the Twilight saga sucks, why is it not here?
" 
 ::Не возражаю.   "
:Oh, and I am in now way upset, nor do I need or wish to be told to relax take a deep breath. Are you always this condescending? Please keep your personal opinions about me to yourself. I prefer that if you have any problems with my edits, you address them individually on the talk page of each article involved rather than posting condescending bullshit on my talk page. Per WP:NPA, we should be discussing the content, not personalities.
emma is a drunken trollop.
: Both versions. Anything I can help with the article my friend?
This is one of the most moronic things I've ever seen. Get a life.
== isotope discrimination, atmospheric values, canopy effect, up or lc delta? == 

 Just a few of the points missing. I suggest you dele

Apparently one of those issues is *not* NPOV. So therefore we can remove it. Possibly there is an NPOV issue with section 3, so we can add the tag there, and we'll come to that issue later.
" 
 ::okay, I'll keep trying to find more stuff.  Why when I add a link does it makes me do the ""captcha"" thing, it's reeeeeally annoying.  And sorry about the multiple refs thing.  Thanks!!!   "
porn is the best thing since sports
"::::Go to any UFO/alien website, data site. There are reports of Greys, other aliens wearing military types on uniforms. Go to the UFO Casebook:Alien Species or Races and/or go to Malevolent Alien Abduction Research Homepage: Click on Alien Species. Also, on the UFO Casebook site, see also ""Alien Contact"" files. They also have alien reports of aliens in some kind of military uniforms.   

 "
" 
 ::: How's ""Dirty Jew"" controversy or ""Dirty Gypsy"" controversy? ←  "
::Thanks, and good luck. I have no intention of bring this to FAC. I no longer have the time and ener

engineflux was real. the two morons above should be banned.
== Devious Maids == 

 About Devious Maids, what I added was real.. A nice source, the first one about the show, and always have REAL infos.. So bad you deleted all..
" 

 == Wikipedia:Requests for adminship/Ironholds == 

 I wasn't really sure what you meant in your reply to my oppose comment. Could you please clear it up? Thanks ).  "
"OK sorry to be annoying about this section, but I think it has implications for the ""Titles"" subsection that should be addressed. Under ""Titles"" we have a list of games ""that have received press coverage"". I take this to mean mainstream press coverage and not random blogs or academic sources. If so, then I suggest that we rename ""Titles"" to ""Notable titles"" and that we remove Lobster Liberation and Revenge of the PETA Tomatoes from the list so it starts with Super Chick Sisters - the first game to receive more mainstream press coverage. Does that sound good? -   

 "
==Progress of im

 *Now that the 2012 and beyond in film page has changed to the 2013 and beyond in film page, this is the first result when you search for ""2011 in film"" on Google. It still seems odd that it wasn't before, though."
" 

 :Being cattle raisers is hardly a ""skeleton in the closet"" but even if it were, Wikipedia is not censored. It was an occupation and it applied to the Yadavs, so it is not ""wrong"" to mention it either. There were plenty of other occupations and so it is worthwhile noting what they were rather than what they were not - it makes for a shorter article ) For example, they were not generally perceived as being fishermen, sailors, barbers, minstrels, temple servants ... the list of what they generally were not is endless. -   "
" 

 == Edit summary == 

 You're right. Responded my talk page. Basically, when told by parties that they don't need to include everything in the source, despite that being the only source they have, because it's ""crufty"", after seeing them in 

...

 and more searching. Probably they will all have problems to be accepted, won't they?
" 
 ::::I read the whole, you should've mentioned the archive2. I think we have already stated the Indian consensus on the first line of section, ""demographics"", I wouldn't have any issue with the current situation of the article. Anything else should be discussed on the talk page first. Happy editing.   •  • Log) "
" 
 :::Clearly, not carefully enough, as #5 was not ""well-sourced"". As well, it did not have the ""widest support,"" and furthermore could not be used, as it violated wiki policy, specifically, WP:LEAD and WP:N. I wasn't the only person to point that out, as not only the mediator pointed that out, but others as well, including Agha Nader and myself; it is worth noting that Agha Nader usually disagree rather vehemently on a wide range of topics. That we found agreement on this is significant, and should be telling you something.  
 :::Rather than expend your energies on a choice we cann

 : Yea, I know, but I thought it's not a problem as long as I properly attribute the source in the edit summary wile merging (just like when merging articles).   "
== Revert war over picture in info box == 

 Would you guys not rather talk about it here?
:I have personally emailed a request to Jimbo.
joel glazerr is gay anf fat and giner
Whomever blocked me is a the gayest person on Earth and loves to rape any male living organism.  He also loves to rape his own father repeatedly.
Walt Disney was a mexican americanThe
" 
 :That doesn't explain your other edits.  "
It's both stupid and offensive.
== Real estate tycoon L J Hooker was a Chinese Australian ==
::Great to hear! We need more articles of this quality. I'm looking forward to future collaboration. }
" 
 This evening she said the humorless didn't get it and ""that shows (1) race is still volatile, and (2) FoxNews and ""your's truly"" are targets.""   She was responding to another who was kidding. —   "
== My email == 

 Yeah sure

"?  Yes all of yours (the collective form of the word ""yours"") were..."
" 

 == Your opinion == 

 Wikipedia:Possibly unfree images/2009 February 27#File:Empro1.jpg - I am not always very clear on the grayer areas of copyright, would you mind commenting on this image? Is the ad original and creative? Would this image need to be fair use? Thanks. ▫ '''''' "
KEANU MOTHERFUCKING MARTUCCIO LOVES KILLING FRANKIE HE IS SHIT AT THE GAME I WILL SLAP YOUR HEAD NIGGA
:::I'm still here, though I probably will have next to nil time to help on collabs.
Entry for whites policy be ended.
ah ok !!! malaki ung suso ni mich nunez!!
==August 2011== 
 Once again, please do not add links that go nowhere or, worse, go to articles that are not about a given actor. For example this Tim McKenzie goes to a fighter in MMA not an actor from the film Gallipoli. Continuing to add links that are not useful can be considered disruptive editing for which you can be blocked. Your help in this will be appreciated.  |


" 

  Please do not vandalize pages, as you did with this edit to Methadone. If you continue to do so, you will be blocked from editing.  '''''' "
rubbed his ballsack sensually
== Meese == 
 Hey, I see you've blocked the Meese page from ever being created (because of a stupid 'moose' pun), but I think it should be a redirect page to Meese (band).  Thanks!
:::I just rechecked some other sources - I think he should be correctly spelt Hannyngton- I am adding additional sources.
==Re: Franco-Dahomean Wars== 
 It is no problems; I have found that I am a much more talented editor than writer. I might even do some addition later on as one of my favourite books, Douglas Porchs “The French Foreign Legion”, devout a chapter to the war. Like the “Amazons of Black Sparta” it is a study of a group of warriors, albeit a rather different group. My speciality is French military history and, by being a native, Swedish. So if you need any help in those areas just leave a message.
:::::Sure you don't hav

 This car IS the Alienware car.
randy orten is a liar he dosen't have IED and he smells like poop
August 2013 (UTC) 
 : Hell no! Celebrities need to die in a fire, I don't go anywhere near them or their Wikipedia articles.   00:30, 21
:::::::::::You presume wrong. If material remains unchallenged in Wikipedia for long enough, it has gained consensus. As per policy linked to multiple times. You need to gain consensus to remove longstanding content, especially when WP:BRD has come into play. Arguing out of personal convictions, no matter how forcefully expressed, isn't a good substitute for over-riding wikipolicy developed over the years.
" 

 == A Son of Phyllis Schlafly == 

 In the first sentence I'd like to see the egregious Andy Schlafly described as ""a son of..."" Phyllis, even though she has at times spoken of ""my son the lawyer,"" giving the impression she only acknowledged one son. 
 
 John, the nurse, is an Internet acquaintance from when we were both studying pathology onlin

In [35]:
def input_fn_builder(features, seq_length, is_training, drop_remainder):
  """Creates an `input_fn` closure to be passed to TPUEstimator."""

  all_input_ids = []
  all_input_mask = []
  all_segment_ids = []
  all_label_ids = []

  for feature in features:
    all_input_ids.append(feature.input_ids)
    all_input_mask.append(feature.input_mask)
    all_segment_ids.append(feature.segment_ids)
    all_label_ids.append(feature.label_ids)

  def input_fn(params):
    """The actual input function."""
    batch_size = params["batch_size"]

    num_examples = len(features)

    # This is for demo purposes and does NOT scale to large data sets. We do
    # not use Dataset.from_generator() because that uses tf.py_func which is
    # not TPU compatible. The right way to load data is with TFRecordReader.
    d = tf.data.Dataset.from_tensor_slices({
        "input_ids":
            tf.constant(
                all_input_ids, shape=[num_examples, seq_length],
                dtype=tf.int32),
        "input_mask":
            tf.constant(
                all_input_mask,
                shape=[num_examples, seq_length],
                dtype=tf.int32),
        "segment_ids":
            tf.constant(
                all_segment_ids,
                shape=[num_examples, seq_length],
                dtype=tf.int32),
        "label_ids":
            tf.constant(all_label_ids, shape=[num_examples, len(LABEL_COLUMNS)], dtype=tf.int32),
    })

    if is_training:
      d = d.repeat()
      d = d.shuffle(buffer_size=100)

    d = d.batch(batch_size=batch_size, drop_remainder=drop_remainder)
    return d

  return input_fn

In [36]:
print('Beginning Predictions!')
current_time = datetime.now()

predict_input_fn = input_fn_builder(features=test_features, seq_length=MAX_SEQ_LENGTH, is_training=False, drop_remainder=False)
predictions = estimator.predict(predict_input_fn)
print("Prediction took time ", datetime.now() - current_time)

Beginning Predictions!
Prediction took time  0:00:00.009021


In [37]:
def create_output(predictions):
    probabilities = []
    for (i, prediction) in enumerate(predictions):
        preds = prediction["probabilities"]
        probabilities.append(preds)
    dff = pd.DataFrame(probabilities)
    dff.columns = LABEL_COLUMNS
    
    return dff
        

In [38]:
output_df = create_output(predictions)
merged_df =  pd.concat([x_test, output_df], axis=1)
submission = merged_df.drop(['comment_text'], axis=1)
submission.to_csv("sample_submission0.csv", index=False)

INFO:tensorflow:Calling model_fn.


I0516 19:10:27.751698 15132 tf_logging.py:115] Calling model_fn.


INFO:tensorflow:num_labels:6;logits:Tensor("loss/BiasAdd:0", shape=(?, 6), dtype=float32);labels:Tensor("loss/Cast:0", shape=(?, 6), dtype=float32)


I0516 19:10:29.967725 15132 tf_logging.py:115] num_labels:6;logits:Tensor("loss/BiasAdd:0", shape=(?, 6), dtype=float32);labels:Tensor("loss/Cast:0", shape=(?, 6), dtype=float32)


INFO:tensorflow:**** Trainable Variables ****


...

I0516 19:10:31.324698 15132 tf_logging.py:115] Restoring parameters from ./working/output\model.ckpt-312


INFO:tensorflow:Running local_init_op.


I0516 19:10:32.037698 15132 tf_logging.py:115] Running local_init_op.


INFO:tensorflow:Done running local_init_op.


I0516 19:10:32.094697 15132 tf_logging.py:115] Done running local_init_op.


In [39]:
submission.head()

id     toxic  severe_toxic   obscene    threat    insult  \
0  d0ce1a57b9e4d96a  0.808328      0.063720  0.492975  0.030006  0.520473   
1  d0ce6a1880c92388  0.334235      0.013414  0.069393  0.010234  0.101430   
2  d0ce76833b320469  0.021030      0.005208  0.010206  0.006089  0.010597   
3  d0cecbf6296fc0a4  0.880328      0.119387  0.679688  0.050053  0.668441   
4  d0cefca8447b6637  0.020634      0.004988  0.009900  0.006099  0.010605   

   identity_hate  
0       0.049980  
1       0.015801  
2       0.006917  
3       0.087278  
4       0.006870

##### Thanks for Reading, most of the code is from below examples

https://github.com/google-research/bert/blob/master/run_classifier.py

https://github.com/yajian/bert/blob/master/run_multilabels_classifier.py